
# Connectivity matrices

`siibra` provides access to parcellation-averaged connectivity matrices.
Several types of connectivity are supported. As of now, these include
"StreamlineCounts", "StreamlineLengths", "FunctionalConnectivity", and
"AnatomoFunctionalConnectivity" (F-Tract).


In [ ]:
from nilearn import plotting
import siibra

We start by selecting an atlas parcellation.



In [ ]:
julich_brain = siibra.parcellations.get("julich 2.9")

The matrices are queried as expected, using `siibra.features.get`, passing
the parcellation as a concept. Here, we query for structural connectivity matrices.
Since a single query may yield hundreds of connectivity matrices for different
subjects of a cohort, siibra groups them as elements into
`sphx_glr_examples_03_data_features_009_compound_features.py`.
Let us select "HCP" cohort.



In [ ]:
features = siibra.features.get(julich_brain, siibra.features.connectivity.StreamlineCounts)
for f in features:
    print(f.name)
    if f.cohort == "HCP":
        cf = f
        print(f"Selected: {cf.name}'\n'" + cf.description)

We can select a specific element by integer index



In [ ]:
print(cf[0].name)
print(cf[0].subject)  # Subjects are encoded via anonymized ids

The connectivity matrices are provided as pandas DataFrames, with region
objects as indices and columns. We can access the matrix corresponding to
the selected index by



In [ ]:
matrix = cf[0].data
matrix.iloc[0:15, 0:15]  # let us see the first 15x15

The matrix can be displayed using `plot` method. In addition, it can be
displayed only for a specific list of regions.



In [ ]:
selected_regions = cf[0].regions[0:30]
cf[0].plot(regions=selected_regions, reorder=True, cmap="magma")

We can create a 3D visualization of the connectivity using
the plotting module of [nilearn](https://nilearn.github.io).
To do so, we need to provide centroids in
the anatomical space for each region (or "node") of the connectivity matrix.



In [ ]:
node_coords = cf[0].compute_centroids('mni152')

Now we can plot the structural connectome.



In [ ]:
view = plotting.plot_connectome(
    adjacency_matrix=matrix,
    node_coords=node_coords,
    edge_threshold="80%",
    node_size=10,
)
view.title(
    f"{cf.modality} of subject {cf.indices[0]} in {cf[0].cohort} cohort "
    f"averaged on {julich_brain.name}",
    size=10,
)

or in 3D:



In [ ]:
plotting.view_connectome(
    adjacency_matrix=matrix,
    node_coords=node_coords,
    edge_threshold="99%",
    node_size=3, colorbar=False,
    edge_cmap="bwr"
)

You can also access to F-Tract atlases using `siibra`. Unlike the most
connectivity matrices in siibra, F-Tract matrices are subject-averaged but
distinguished by their "feature".



In [ ]:
ftract = siibra.features.get(
    siibra.parcellations.get("julich 3.0"),
    siibra.features.connectivity.AnatomoFunctionalConnectivity
)[0]  # also compounded
print(ftract.cohort)
print(ftract.name)
print("indexing attributes:", ftract.indexing_attributes)
for f in ftract:
    print(f.feature)

We can similarly draw the data as above. This time let us get the element by
its feature name



In [ ]:
f = ftract.get_element("P_11: speed__euclidian__peak_delay__median")
f.plot()